In [2]:
!pip install numba

add video and other visual methods

# final fixed version

In [9]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

#%% Corrected Particle System
class Particles:
    def __init__(self, dim, num_particles):
        self.dim = dim
        self.N = num_particles
        self.positions = np.random.randn(dim, num_particles) * 5.0  # Expand the initial dispersion range
        self.velocities = np.zeros((dim, num_particles))
        self.forces = np.zeros((dim, num_particles))
    
    def get_position(self, i):
        return self.positions[:, i]
    
    def kinetic_energy(self):
        return 0.5 * np.sum(self.velocities**2)

#%% Corrected LeapFrog Integrator
class LeapFrogIntegrator:
    def __init__(self):
        self.energy_history = []
    
    def integrate(self, particles, pair_force, confinement_force, step_size):
        dim, N = particles.dim, particles.N
        half_step = 0.5 * step_size
        
        # 1. Update half-step velocity
        particles.velocities += half_step * particles.forces
        
        # 2. Update positions
        particles.positions += step_size * particles.velocities
        
        # 3. Compute new forces
        new_forces = np.zeros((dim, N))
        
        # Confinement force
        for i in range(N):
            pos = particles.get_position(i)
            new_forces[:, i] = confinement_force(pos)
        
        # Pairwise force
        for i in range(N):
            for j in range(i+1, N):
                r_vec = particles.get_position(i) - particles.get_position(j)
                r = np.linalg.norm(r_vec)
                f_mag = pair_force(r)
                force = f_mag * r_vec / (r + 1e-6)
                new_forces[:, i] += force
                new_forces[:, j] -= force
        
        # 4. Update second half-step velocity
        particles.velocities += half_step * new_forces
        particles.forces = new_forces

#%% Dynamic Visualization (Auto-adjust Axis)
def create_animation(trajectory_data):
    fig, ax = plt.subplots(figsize=(8, 8))
    scat = ax.scatter([], [], alpha=0.5)
    
    def init():
        ax.set_xlim(-10, 10)
        ax.set_ylim(-10, 10)
        return scat,
    
    def animate(i):
        scat.set_offsets(trajectory_data[i].T)
        ax.set_title(f"Step {i*100}")
        return scat,
    
    ani = FuncAnimation(fig, animate, init_func=init, frames=len(trajectory_data), interval=50)
    plt.close()
    return HTML(ani.to_jshtml())

#%% Parameter Adjustment & Execution
if __name__ == "__main__":
    # Parameter settings
    dim = 2
    N = 5                  # Reduce the number of particles for better observation
    step_size = 0.01       # Increase the step size
    total_steps = 5000     # Reduce the total number of steps
    
    # Initialize the system
    particles = Particles(dim, N)
    integrator = LeapFrogIntegrator()
    
    # Define a stronger force field
    def pair_force(r):
        return -1.0 / (r + 1e-6)  # Increase the repulsion coefficient
    
    def confinement_force(pos):
        return -0.1 * pos         # Weaken the confinement force
    
    # Run the simulation
    simulator = IPS_Simulator(particles, pair_force, confinement_force, integrator)
    trajectory = simulator.run_simulation(total_steps, step_size, output_interval=10)  # Increase output frequency
    
    # Display animation
    ani = create_animation(trajectory)
    display(ani)
    
    # Print position changes for verification
    print("Initial position:\n", trajectory[0])
    print("End position:\n", trajectory[-1])


Initial position:
 [[ -5.60773156  -6.8567116    0.89303285  -0.82669831   0.9699821 ]
 [-10.52464048   7.53471474  -4.17461141   2.70923252  -1.13725901]]
End position:
 [[  1.12756613   1.26883154   3.49966009   3.95176309   1.54955729]
 [-10.90854795   2.46883008   5.24215275   4.31044631   4.46463514]]


# May be Better

In [12]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

#%% Enhanced Particle System Class
class Particles:
    def __init__(self, dim, num_particles):
        self.dim = dim
        self.N = num_particles
        self.positions = np.random.randn(dim, num_particles) * 5.0  # Initialize with wider spread
        self.velocities = np.zeros((dim, num_particles))
        self.forces = np.zeros((dim, num_particles))
    
    def get_position(self, i):
        return self.positions[:, i]
    
    def kinetic_energy(self):
        return 0.5 * np.sum(self.velocities**2)

#%% Leapfrog Integrator Class
class LeapFrogIntegrator:
    def __init__(self):
        self.energy_history = []
    
    def integrate(self, particles, pair_force, confinement_force, step_size):
        dim, N = particles.dim, particles.N
        half_step = 0.5 * step_size
        
        # 1. Update half-step velocities
        particles.velocities += half_step * particles.forces
        
        # 2. Update positions
        particles.positions += step_size * particles.velocities
        
        # 3. Calculate new forces
        new_forces = np.zeros((dim, N))
        
        # Confinement forces
        for i in range(N):
            pos = particles.get_position(i)
            new_forces[:, i] = confinement_force(pos)
        
        # Pairwise forces
        for i in range(N):
            for j in range(i+1, N):
                r_vec = particles.get_position(i) - particles.get_position(j)
                r = np.linalg.norm(r_vec)
                f_mag = pair_force(r)
                force = f_mag * r_vec / (r + 1e-6)  # Prevent division by zero
                new_forces[:, i] += force
                new_forces[:, j] -= force
        
        # 4. Update velocities with new forces
        particles.velocities += half_step * new_forces
        particles.forces = new_forces

#%% Animation Function with Dynamic Scaling
def create_animation(trajectory_data):
    fig, ax = plt.subplots(figsize=(10, 10))  # Larger figure size
    scat = ax.scatter([], [], alpha=0.5)
    
    # Calculate dynamic axis limits
    x_min, x_max = np.min(trajectory_data[:,0,:]), np.max(trajectory_data[:,0,:])
    y_min, y_max = np.min(trajectory_data[:,1,:]), np.max(trajectory_data[:,1,:])
    margin = 2.0  # Add 20% margin
    
    def init():
        ax.set_xlim(x_min - margin, x_max + margin)
        ax.set_ylim(y_min - margin, y_max + margin)
        return scat,
    
    def animate(i):
        scat.set_offsets(trajectory_data[i].T)
        ax.set_title(f"Step {i*10}", fontsize=12)
        return scat,
    
    ani = FuncAnimation(fig, animate, init_func=init, frames=len(trajectory_data), interval=50)
    plt.close()
    return HTML(ani.to_jshtml())

#%% Main Simulation Parameters and Execution
if __name__ == "__main__":
    # Simulation parameters
    dim = 2
    N = 5
    step_size = 0.1
    total_steps = 500
    
    # Initialize system
    particles = Particles(dim, N)
    integrator = LeapFrogIntegrator()
    
    # Force definitions
    def pair_force(r):
        return -1.0 / (r + 1e-6)  # Strong repulsive force
    
    def confinement_force(pos):
        return -0.1 * pos  # Mild harmonic confinement
    
    # Run simulation
    simulator = IPS_Simulator(particles, pair_force, confinement_force, integrator)
    trajectory = simulator.run_simulation(total_steps, step_size, output_interval=10)
    
    # Display results
    display(create_animation(trajectory))
    
    # Position verification
    print("Initial positions:\n", trajectory[0])
    print("\nFinal positions:\n", trajectory[-1])

Initial positions:
 [[ 0.8075211   0.71497681  0.15967683  1.3653229  -5.39700823]
 [ 9.3622328  -6.78722782  2.26136037  3.99708079 10.62946917]]

Final positions:
 [[ -2.49850044  -1.85390078   0.83691172 -46.52292297  52.34306806]
 [ -4.66396649  -7.86720157  -4.77227549 -32.32831695  30.54041576]]
